# Coursera Data Science Capstone
### Battle of the Neighborhoods - Final Project

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction <a name="introduction"></a>


In this final project, we will explore the optimal location for adding four food service stores in Chicago, IL, USA. These are stores designed to be suppliers for area restaurants.

We want these four stores to be **in areas with dense clusters of restaurants** to maximize the potential customer base. These stores should also be **evenly spread throughout the city** to maximize the footprint throughout the city. Lastly, according to the principles of game theory and the Nash equilibrium, we will want to consider **close proximity to existing food service stores** of competitors.

We will using data science methodology to find 4 suitible locations to open food service stores.

In [1]:
import pandas as pd
import numpy as np

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


## Data <a name="data"></a>

First we need to get regional data for Chicago, IL.Since our service area will include surrounding metro Chicago, we will get a list of neighborhoods. Chicago has Neighborhoods as a subset of the Community Area, but for this analysis, we will consider the Community Area as "Neighborhood" going forth. We will **pull a list of the neighborhoods data** from the "List of Neighborhoods in Chicago" wikipedia page to use as our research areas.

### Neighborhood List

In [87]:
# Read the table from the Wiki page into a DataFrame
chi_wiki = pd.read_html('https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago')

In [88]:
chi_df = chi_wiki[0]
chi_df

Neighborhood  Community area
0             Albany Park     Albany Park
1         Altgeld Gardens       Riverdale
2           Andersonville       Edgewater
3          Archer Heights  Archer Heights
4           Armour Square   Armour Square
..                    ...             ...
241              Wildwood     Forest Glen
242              Woodlawn        Woodlawn
243            Wrightwood         Ashburn
244  Wrightwood Neighbors    Lincoln Park
245          Wrigleyville       Lake View

[246 rows x 2 columns]

Now that we have our data, we will need to cleanse our data into a usable format. First, we will drop duplicate community areas to narrow down our search. Next, we will drop the "Neighborhood" column so we're only left with our Community Area. Finally, we will drop the astrisk from the County field.

**We will now refer to the community area as neighborhoods.**

In [89]:
chi_df = chi_df.drop_duplicates(subset=['Community area'],ignore_index=True)
chi_df = chi_df.drop(labels='Neighborhood', axis=1)
chi_df

Community area
0             Albany Park
1               Riverdale
2               Edgewater
3          Archer Heights
4           Armour Square
..                    ...
77         West Englewood
78     West Garfield Park
79  Austin, Humboldt Park
80           West Pullman
81               Woodlawn

[82 rows x 1 columns]

Now that we have our Wikipedia table data cleaned up, let's extract a list of the counties so we can use the list to find coordinates of each.

In [90]:
# Creating a List of neighborhoods from the DataFrame data
neighborhoods = chi_df['Community area'].tolist()
neighborhoods

['Albany Park',
 'Riverdale',
 'Edgewater',
 'Archer Heights',
 'Armour Square',
 'Ashburn',
 'Auburn Gresham',
 'Avalon Park',
 'Avondale',
 'Irving Park',
 'New City',
 'Belmont Cragin',
 'Hermosa',
 'Dunning',
 'Beverly',
 'Morgan Park',
 'Norwood Park',
 'Lake View',
 'Lincoln Square',
 'Washington Heights',
 'Bridgeport',
 'Brighton Park',
 'Douglas',
 'Logan Square',
 'Uptown',
 'Burnside',
 'Near North Side',
 'Calumet Heights',
 'Near South Side',
 'Chatham',
 'Chicago Lawn',
 'Clearing',
 'Pullman',
 'North Lawndale',
 'East Garfield Park',
 'Hyde Park',
 'Lower West Side',
 'East Side',
 'West Town',
 'Forest Glen',
 'Edison Park',
 'Englewood',
 'Roseland',
 'West Lawn',
 'Fuller Park',
 'Near West Side',
 'Gage Park',
 'Austin',
 'Garfield Ridge',
 'Jefferson Park',
 'Grand Boulevard',
 'Greater Grand Crossing',
 'Hegewisch',
 'North Park',
 'Humboldt Park',
 'South Shore',
 'Kenwood',
 'Lincoln Park',
 'South Lawndale',
 'The Loop',
 'Rogers Park',
 'McKinley Park',
 'Mont

### Neighborhood Coordinates

Now that we have our list, let's create a dataframe and initate the dataframe column names.

In [6]:
# Define the dataframe columns
column_names = ['Neighborhood', 'Latitude', 'Longitude'] 

# Label the columns in the dataframe
neighborhood_loc_data = pd.DataFrame(columns=column_names)

In [7]:
    address = 'Edgewater, Chicago, IL'

    geolocator = Nominatim(user_agent="ny_explorer")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    
    # In case there is an error in the coordinates returned, we will ignore that value
    
    if not 41 < latitude < 43:
            latitude = np.nan
            print(latitude)
            
    if not -88 < longitude < -86:
            longitude = np.nan
            print(longitude)
    
print('Latitude =',latitude)
print('Longitude =', longitude)

Latitude = 41.9833689
Longitude = -87.6639516


We will loop through each county in the list and populate our dataframe with county and coordinates data. Due to Nominatim's user agreement, we will need to pause for 1 sec during each loop.

In [8]:
from time import sleep

for neighborhood in neighborhoods:
    
    address = neighborhood + ', Chicago, IL'

    geolocator = Nominatim(user_agent="ny_explorer")
    location = geolocator.geocode(address)

    try:
        latitude = location.latitude
        longitude = location.longitude
    except:
        address = neighborhood + ', IL'
        geolocator = Nominatim(user_agent="ny_explorer")
        location = geolocator.geocode(address)
        try:
            latitude = location.latitude
            longitude = location.longitude
        except:
            latitude = np.nan
            longitude = np.nan
            
    if not 41 < latitude < 43:
            latitude = np.nan
            
    if not -88 < longitude < -86:
            longitude = np.nan
    
    neighborhood_loc_data = neighborhood_loc_data.append({'Neighborhood': neighborhood,
                                          'Latitude': latitude,
                                          'Longitude': longitude}, ignore_index=True)
     
    
    sleep(1)

In [9]:
neighborhood_loc_data

Neighborhood   Latitude  Longitude
0             Albany Park  41.971937 -87.716174
1               Riverdale  41.667835 -87.604964
2               Edgewater  41.983369 -87.663952
3          Archer Heights  41.811422 -87.726165
4           Armour Square  41.840033 -87.633107
..                    ...        ...        ...
77         West Englewood  41.778089 -87.666718
78     West Garfield Park  41.880588 -87.729223
79  Austin, Humboldt Park  41.895125 -87.741004
80           West Pullman  41.671775 -87.638358
81               Woodlawn  41.779479 -87.599493

[82 rows x 3 columns]

In [10]:
# Dropping two records that have returned errors when fetching coordinates data.
neighborhood_loc_data.dropna(inplace=True)
neighborhood_loc_data

Neighborhood   Latitude  Longitude
0             Albany Park  41.971937 -87.716174
1               Riverdale  41.667835 -87.604964
2               Edgewater  41.983369 -87.663952
3          Archer Heights  41.811422 -87.726165
4           Armour Square  41.840033 -87.633107
..                    ...        ...        ...
77         West Englewood  41.778089 -87.666718
78     West Garfield Park  41.880588 -87.729223
79  Austin, Humboldt Park  41.895125 -87.741004
80           West Pullman  41.671775 -87.638358
81               Woodlawn  41.779479 -87.599493

[80 rows x 3 columns]

In [11]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None): 
    print(neighborhood_loc_data)

               Neighborhood   Latitude  Longitude
0               Albany Park  41.971937 -87.716174
1                 Riverdale  41.667835 -87.604964
2                 Edgewater  41.983369 -87.663952
3            Archer Heights  41.811422 -87.726165
4             Armour Square  41.840033 -87.633107
5                   Ashburn  41.747533 -87.711163
6            Auburn Gresham  41.743387 -87.656042
7               Avalon Park  41.745035 -87.588658
8                  Avondale  41.938921 -87.711168
9               Irving Park  41.953365 -87.736447
10                 New City  41.807533 -87.656440
11           Belmont Cragin  41.931698 -87.768670
12                  Hermosa  41.928643 -87.734502
13                  Dunning  41.952809 -87.796449
14                  Beverly  41.718153 -87.671767
15              Morgan Park  41.686531 -87.668961
16             Norwood Park  41.985590 -87.800582
17                Lake View  41.947050 -87.655429
18           Lincoln Square  41.975990 -87.689616


In [12]:
# We will find the avg for Lat and Lon in order to center our map
latitude = neighborhood_loc_data['Latitude'].mean(axis=0)
longitude = neighborhood_loc_data['Longitude'].mean(axis=0)
print('Latitude =',latitude)
print('Longitude =', longitude)

Latitude = 41.845609759374994
Longitude = -87.67755249822562


### Map of Neighborhoods

In [13]:
# create map of Chicago using latitude and longitude values
map_chi = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(neighborhood_loc_data['Latitude'], neighborhood_loc_data['Longitude'], neighborhood_loc_data['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_chi)  
    
map_chi

### Foursquare Data - Surrounding Restaurants

Define Foursquare Credentials and Version

In [14]:
CLIENT_ID = 'BXUCPOEUBAZMUJNQU4Q1D1CD2K5BL4BLFSDMLDUQRMW0EVFM' # your Foursquare ID
CLIENT_SECRET = '4JGHXK0PMSZBUWDZIYC0NKJA1GA3W2MSYDO2QJG1LSY3KILY' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [15]:
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues



In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL

        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            food_category,
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)
print('Complete!')

In [17]:
chi_venues = getNearbyVenues(names=neighborhood_loc_data['Neighborhood'], latitudes=neighborhood_loc_data['Latitude'], longitudes=neighborhood_loc_data['Longitude'])

Albany Park
Riverdale
Edgewater
Archer Heights
Armour Square
Ashburn
Auburn Gresham
Avalon Park
Avondale
Irving Park
New City
Belmont Cragin
Hermosa
Dunning
Beverly
Morgan Park
Norwood Park
Lake View
Lincoln Square
Washington Heights
Bridgeport
Brighton Park
Douglas
Logan Square
Uptown
Burnside
Near North Side
Calumet Heights
Near South Side
Chatham
Chicago Lawn
Clearing
Pullman
North Lawndale
East Garfield Park
Hyde Park
Lower West Side
East Side
West Town
Forest Glen
Edison Park
Englewood
Roseland
West Lawn
Fuller Park
Near West Side
Gage Park
Austin
Garfield Ridge
Jefferson Park
Grand Boulevard
Hegewisch
North Park
Humboldt Park
South Shore
Kenwood
Lincoln Park
South Lawndale
The Loop
Rogers Park
McKinley Park
Montclare
Mount Greenwood
North Center
West Ridge
Oakland
O'Hare
West Town, Logan Square
Avondale, Irving Park
Portage Park
Lakeview
South Chicago
South Deering
Washington Park
West Elsdon
West Englewood
West Garfield Park
Austin, Humboldt Park
West Pullman
Woodlawn


In [32]:
print(chi_venues.shape)
chi_venues.head()

(1050, 8)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Albany Park              41.971937              -87.716174   
1  Albany Park              41.971937              -87.716174   
2  Albany Park              41.971937              -87.716174   
3  Albany Park              41.971937              -87.716174   
4  Albany Park              41.971937              -87.716174   

                       Venue  Venue Latitude  Venue Longitude  \
0  Peking Mandarin Resturant       41.968292       -87.715783   
1  Popeyes Louisiana Kitchen       41.968756       -87.713019   
2                  Banpojung       41.975707       -87.715609   
3                     Subway       41.968748       -87.712861   
4                    Dunkin'       41.968255       -87.712964   

        Venue Category  Distance  
0   Chinese Restaurant  0.310926  
1  Fried Chicken Joint  0.310926  
2    Korean Restaurant  0.310926  
3       Sandwich Place  0.310926  
4           Donut Shop  0.310926

### Distance of Venues to each Neighborhood

In [77]:
chi_venues_dist = pd.DataFrame()

In [78]:
import geopy.distance

for lat, lng, neighborhood in zip(neighborhood_loc_data['Latitude'], neighborhood_loc_data['Longitude'], neighborhood_loc_data['Neighborhood']):
    coords_1 = (lat, lng)
    for i, row in chi_venues.iterrows():
        coords_2 = (row['Venue Latitude'], row['Venue Longitude'])
        print(coords_1 ,coords_2)

        chi_venues_dist.loc[i,neighborhood] = geopy.distance.distance(coords_1, coords_2).miles

(41.9719367, -87.7161739) (41.96829199927995, -87.71578270440223)
(41.9719367, -87.7161739) (41.96875578368875, -87.7130188002769)
(41.9719367, -87.7161739) (41.975706809962226, -87.7156087405049)
(41.9719367, -87.7161739) (41.968747752852146, -87.71286141717928)
(41.9719367, -87.7161739) (41.96825461681716, -87.71296354370037)
(41.9719367, -87.7161739) (41.968176, -87.71365300000001)
(41.9719367, -87.7161739) (41.968398, -87.71767)
(41.9719367, -87.7161739) (41.975984000000004, -87.715588)
(41.9719367, -87.7161739) (41.96847, -87.71957)
(41.9719367, -87.7161739) (41.968665, -87.71234799999999)
(41.9719367, -87.7161739) (41.975815349205185, -87.71322646225258)
(41.9719367, -87.7161739) (41.982576786499585, -87.65995217377899)
(41.9719367, -87.7161739) (41.983699907992715, -87.65956847389438)
(41.9719367, -87.7161739) (41.98350095066181, -87.66893847298064)
(41.9719367, -87.7161739) (41.98422386195043, -87.66893246706415)
(41.9719367, -87.7161739) (41.983726223431916, -87.65944453877363

(41.9719367, -87.7161739) (41.979229, -87.693363)
(41.9719367, -87.7161739) (41.71550199029488, -87.64358621871719)
(41.9719367, -87.7161739) (41.715586, -87.643574)
(41.9719367, -87.7161739) (41.715901, -87.642725)
(41.9719367, -87.7161739) (41.71387106436069, -87.64114319442534)
(41.9719367, -87.7161739) (41.710321755847886, -87.6427910732974)
(41.9719367, -87.7161739) (41.83720331668269, -87.65103647881698)
(41.9719367, -87.7161739) (41.83809251863777, -87.6510015422747)
(41.9719367, -87.7161739) (41.833666762017295, -87.65105663120234)
(41.9719367, -87.7161739) (41.83712535426352, -87.64617711009907)
(41.9719367, -87.7161739) (41.83603274418493, -87.64615227973619)
(41.9719367, -87.7161739) (41.83700678646905, -87.65118619579194)
(41.9719367, -87.7161739) (41.83878982989852, -87.64637537658106)
(41.9719367, -87.7161739) (41.839296000000004, -87.646989)
(41.9719367, -87.7161739) (41.837708952979334, -87.64592091473253)
(41.9719367, -87.7161739) (41.83667, -87.65136)
(41.9719367, -87

(41.9719367, -87.7161739) (41.85409927368164, -87.62699890136719)
(41.9719367, -87.7161739) (41.85970881399682, -87.62373010897014)
(41.9719367, -87.7161739) (41.85380414858133, -87.62688800613884)
(41.9719367, -87.7161739) (41.853683000000004, -87.626754)
(41.9719367, -87.7161739) (41.8536354489652, -87.62674150793458)
(41.9719367, -87.7161739) (41.854485, -87.621278)
(41.9719367, -87.7161739) (41.853159999999995, -87.624207)
(41.9719367, -87.7161739) (41.853159999999995, -87.624207)
(41.9719367, -87.7161739) (41.853075, -87.624231)
(41.9719367, -87.7161739) (41.85312946649764, -87.6237821842373)
(41.9719367, -87.7161739) (41.85332489013672, -87.6224365234375)
(41.9719367, -87.7161739) (41.854249, -87.620579)
(41.9719367, -87.7161739) (41.85268, -87.62458)
(41.9719367, -87.7161739) (41.856282, -87.63048)
(41.9719367, -87.7161739) (41.86000442504883, -87.62846374511719)
(41.9719367, -87.7161739) (41.73674056104464, -87.61256230679408)
(41.9719367, -87.7161739) (41.744112, -87.61435)
(4

(41.9719367, -87.7161739) (41.88128365731805, -87.66544270201172)
(41.9719367, -87.7161739) (41.879354, -87.668954)
(41.9719367, -87.7161739) (41.88035, -87.667066)
(41.9719367, -87.7161739) (41.880036, -87.665089)
(41.9719367, -87.7161739) (41.88131342192907, -87.66518986440065)
(41.9719367, -87.7161739) (41.879097, -87.668882)
(41.9719367, -87.7161739) (41.882989, -87.66991999999999)
(41.9719367, -87.7161739) (41.79385340520012, -87.69347460268102)
(41.9719367, -87.7161739) (41.793853000000006, -87.694771)
(41.9719367, -87.7161739) (41.793545, -87.694521)
(41.9719367, -87.7161739) (41.79369344936696, -87.69428376993544)
(41.9719367, -87.7161739) (41.79382741588864, -87.69358109132456)
(41.9719367, -87.7161739) (41.793712307821046, -87.69356665260912)
(41.9719367, -87.7161739) (41.793447, -87.693176)
(41.9719367, -87.7161739) (41.88735970514373, -87.76525119679047)
(41.9719367, -87.7161739) (41.88698, -87.7647)
(41.9719367, -87.7161739) (41.887258, -87.763779)
(41.9719367, -87.7161739

(41.9719367, -87.7161739) (41.95430984150239, -87.67477845545348)
(41.9719367, -87.7161739) (41.953491588239814, -87.67831251000595)
(41.9719367, -87.7161739) (41.95481, -87.678615)
(41.9719367, -87.7161739) (41.95252277807111, -87.67761308331784)
(41.9719367, -87.7161739) (41.95485516112041, -87.67898529702359)
(41.9719367, -87.7161739) (41.956285114844405, -87.68023563153348)
(41.9719367, -87.7161739) (41.95438, -87.67944)
(41.9719367, -87.7161739) (41.9542205377979, -87.6753749464502)
(41.9719367, -87.7161739) (41.957468, -87.681464)
(41.9719367, -87.7161739) (41.95587006281363, -87.67620149512074)
(41.9719367, -87.7161739) (41.957548271967376, -87.68124913151101)
(41.9719367, -87.7161739) (41.953983306884766, -87.68122863769531)
(41.9719367, -87.7161739) (41.953510824631586, -87.67828792390884)
(41.9719367, -87.7161739) (41.953074, -87.67775999999999)
(41.9719367, -87.7161739) (41.954511, -87.674577)
(41.9719367, -87.7161739) (41.952486, -87.677738)
(41.9719367, -87.7161739) (41.95

...

(41.671775350000004, -87.63835802467068) (41.896901838350175, -87.72159318534891)
(41.671775350000004, -87.63835802467068) (41.902351, -87.718441)
(41.671775350000004, -87.63835802467068) (41.75885967195196, -87.57509849827933)
(41.671775350000004, -87.63835802467068) (41.756594329437505, -87.57594665686513)
(41.671775350000004, -87.63835802467068) (41.758734000000004, -87.57205)
(41.671775350000004, -87.63835802467068) (41.762683, -87.576633)
(41.671775350000004, -87.63835802467068) (41.80975217657005, -87.59811669588089)
(41.671775350000004, -87.63835802467068) (41.81030126129739, -87.59345878948653)
(41.671775350000004, -87.63835802467068) (41.80968966734237, -87.59266982251455)
(41.671775350000004, -87.63835802467068) (41.809826, -87.60345600000001)
(41.671775350000004, -87.63835802467068) (41.80981554285489, -87.59237378708279)
(41.671775350000004, -87.63835802467068) (41.810496, -87.59264)
(41.671775350000004, -87.63835802467068) (41.8103373, -87.5924444)
(41.671775350000004, -87

(41.671775350000004, -87.63835802467068) (41.942809720541554, -87.65307711368148)
(41.671775350000004, -87.63835802467068) (41.94181914533175, -87.65418329513997)
(41.671775350000004, -87.63835802467068) (41.94526903560607, -87.65431632484676)
(41.671775350000004, -87.63835802467068) (41.945084297939154, -87.6547567646194)
(41.671775350000004, -87.63835802467068) (41.94403469646459, -87.6540981750418)
(41.671775350000004, -87.63835802467068) (41.945344542628376, -87.65510197917357)
(41.671775350000004, -87.63835802467068) (41.94192422108425, -87.65233070193084)
(41.671775350000004, -87.63835802467068) (41.943787, -87.65401)
(41.671775350000004, -87.63835802467068) (41.945392, -87.655169)
(41.671775350000004, -87.63835802467068) (41.94658011938799, -87.65590574189893)
(41.671775350000004, -87.63835802467068) (41.94380715192381, -87.64929330584161)
(41.671775350000004, -87.63835802467068) (41.947235986612725, -87.65497950834744)
(41.671775350000004, -87.63835802467068) (41.94352126119235

(41.7794786, -87.599493) (41.97528839111328, -87.68893432617188)
(41.7794786, -87.599493) (41.976119, -87.686963)
(41.7794786, -87.599493) (41.97608939687306, -87.69241227571605)
(41.7794786, -87.599493) (41.976207212013946, -87.69242310857432)
(41.7794786, -87.599493) (41.974693183524806, -87.69221521000402)
(41.7794786, -87.599493) (41.978671000000006, -87.692397)
(41.7794786, -87.599493) (41.979246014764556, -87.69247892286532)
(41.7794786, -87.599493) (41.97916758828641, -87.69288321483447)
(41.7794786, -87.599493) (41.979229, -87.693363)
(41.7794786, -87.599493) (41.71550199029488, -87.64358621871719)
(41.7794786, -87.599493) (41.715586, -87.643574)
(41.7794786, -87.599493) (41.715901, -87.642725)
(41.7794786, -87.599493) (41.71387106436069, -87.64114319442534)
(41.7794786, -87.599493) (41.710321755847886, -87.6427910732974)
(41.7794786, -87.599493) (41.83720331668269, -87.65103647881698)
(41.7794786, -87.599493) (41.83809251863777, -87.6510015422747)
(41.7794786, -87.599493) (41.

(41.7794786, -87.599493) (42.003391, -87.817084)
(41.7794786, -87.599493) (42.002877285288015, -87.81637824701032)
(41.7794786, -87.599493) (42.002957, -87.816939)
(41.7794786, -87.599493) (42.002876, -87.817665)
(41.7794786, -87.599493) (42.00248, -87.816997)
(41.7794786, -87.599493) (41.77998374448471, -87.64511749125887)
(41.7794786, -87.599493) (41.77993920689278, -87.64451116400164)
(41.7794786, -87.599493) (41.779449462890625, -87.64661407470703)
(41.7794786, -87.599493) (41.78051329785532, -87.64237212717268)
(41.7794786, -87.599493) (41.780198999999996, -87.64379699999999)
(41.7794786, -87.599493) (41.780507497587976, -87.64210280335476)
(41.7794786, -87.599493) (41.780169506205574, -87.64240560988478)
(41.7794786, -87.599493) (41.779398, -87.651076)
(41.7794786, -87.599493) (41.78361747022648, -87.64451116410756)
(41.7794786, -87.599493) (41.699676513671875, -87.62765502929688)
(41.7794786, -87.599493) (41.77166, -87.72295)
(41.7794786, -87.599493) (41.77587162137056, -87.7228

(41.7794786, -87.599493) (41.977374606998616, -87.90710449218749)
(41.7794786, -87.599493) (41.97558867229975, -87.90292830729234)
(41.7794786, -87.599493) (41.97572624386532, -87.9033151131779)
(41.7794786, -87.599493) (41.97567954319579, -87.90328245173441)
(41.7794786, -87.599493) (41.97395248819364, -87.90332095344708)
(41.7794786, -87.599493) (41.975374891283586, -87.90333145035908)
(41.7794786, -87.599493) (41.92989890177015, -87.70735955143489)
(41.7794786, -87.599493) (41.930117319140486, -87.70722735226109)
(41.7794786, -87.599493) (41.930452098076884, -87.70963196033523)
(41.7794786, -87.599493) (41.927746625918466, -87.70705775217938)
(41.7794786, -87.599493) (41.93010298916194, -87.70704867011507)
(41.7794786, -87.599493) (41.9297556281864, -87.7072332866658)
(41.7794786, -87.599493) (41.92915967432794, -87.70749347846545)
(41.7794786, -87.599493) (41.930875978615134, -87.71026055520063)
(41.7794786, -87.599493) (41.931535617055566, -87.71147555817222)
(41.7794786, -87.5994

In [79]:
chi_venues_dist

Albany Park  Riverdale  Edgewater  Archer Heights  Armour Square  \
0        0.252353  21.511012   2.864980       10.839870       9.824834   
1        0.273138  21.504407   2.720811       10.879791       9.792875   
2        0.261826  22.002332   2.712269       11.351449      10.284492   
3        0.278475  21.501766   2.713491       10.879746       9.788961   
4        0.303186  21.470269   2.731201       10.845448       9.760311   
...           ...        ...        ...             ...            ...   
1045    21.168606   1.893857  21.634089       10.675891      11.718077   
1046    21.174456   1.911325  21.642435       10.676897      11.728093   
1047    21.227916   1.535307  21.646896       10.820463      11.700807   
1048    14.719613   7.716650  14.541945        7.194261       4.659331   
1049    14.485820   7.674676  14.420990        6.621318       4.444698   

        Ashburn  Auburn Gresham  Avalon Park   Avondale  Irving Park  ...  \
0     15.237759       15.825134    16.746319   2.041011     1.481373  ...   
1     15.268204       15.829425    16.720524   2.061333     1.607737  ...   
2     15.749316       16.325662    17.214788   2.549154     1.878780  ...   
3     15.267601       15.827374    16.716898   2.060420     1.613466  ...   
4     15.233598       15.794910    16.687502   2.026649     1.587268  ...   
...         ...             ...          ...        ...          ...  ...   
1045   6.432933        5.096674     5.831320  18.881886    20.138958  ...   
1046   6.430404        5.103220     5.848175  18.887566    20.143560  ...   
1047   6.634590        5.153328     5.662542  18.944627    20.220605  ...   
1048   6.457117        4.068287     2.380405  12.573717    14.091153  ...   
1049   5.877586        3.588729     2.502597  12.308223    13.798591  ...   

       Lakeview  South Chicago  South Deering  Washington Park  West Elsdon  \
0      3.596563      18.225590      20.452245        13.134767    12.042785   
1      3.486964      18.188045      20.430687        13.110434    12.080919   
2      3.854973      18.675702      20.926449        13.605367    12.554518   
3      3.479633      18.183828      20.427271        13.106891    12.080766   
4      3.467611      18.156022      20.397372        13.077293    12.046512   
...         ...            ...            ...              ...          ...   
1045  18.891336       6.431085       3.909700         8.517641     9.548523   
1046  18.900043       6.450829       3.930252         8.529497     9.548630   
1047  18.897668       6.167401       3.574937         8.464537     9.707931   
1048  11.779909       3.783285       6.116291         1.558539     6.834198   
1049  11.652297       4.152666       6.239885         1.136930     6.232678   

      West Englewood  West Garfield Park  Austin, Humboldt Park  West Pullman  \
0          13.368840            6.092575               5.214338     20.850970   
1          13.374076            6.142121               5.282440     20.855542   
2          13.870014            6.602206               5.713389     21.351733   
3          13.372083            6.142681               5.284128     20.853498   
4          13.339536            6.108246               5.249958     20.821025   
...              ...                 ...                    ...           ...   
1045        7.549393           15.201845              16.343321      0.185739   
1046        7.555434           15.205299              16.346425      0.206278   
1047        7.610942           15.304333              16.451439      0.222046   
1048        3.776463            9.890764              11.032982      7.774275   
1049        3.164012            9.482391              10.635458      7.595295   

       Woodlawn  
0     14.345523  
1     14.315689  
2     14.808161  
3     14.311864  
4     14.282974  
...         ...  
1045   7.836610  
1046   7.850674  
1047   7.735151  
1048   0.302921  
1049   0.310926  

[1050 rows x 80 columns]

### Average Distance to Restaurants within a Neighborhood from Neighborhood center

In [73]:
chi_avg_dist= chi_venues[['Distance','Neighborhood']].groupby('Neighborhood').mean()
chi_avg_dist.rename(columns={'Distance': 'Avg Dist to Restaurants'}, inplace=True)
chi_avg_dist

Avg Dist to Restaurants
Neighborhood                                    
Albany Park                             0.281825
Archer Heights                          0.226497
Armour Square                           0.170620
Ashburn                                 0.232879
Auburn Gresham                          0.148708
...                                          ...
West Pullman                            0.184413
West Ridge                              0.273815
West Town                               0.190187
West Town, Logan Square                 0.165605
Woodlawn                                0.306923

[76 rows x 1 columns]

### Number of Restaurants in Neighborhood

In [72]:
chi_num_rest= chi_venues[['Venue','Neighborhood']].groupby('Neighborhood').count()
chi_num_rest.rename(columns={'Venue': 'Num of Restaurants'}, inplace=True)
chi_num_rest

Num of Restaurants
Neighborhood                               
Albany Park                              11
Archer Heights                           13
Armour Square                            16
Ashburn                                   5
Auburn Gresham                            1
...                                     ...
West Pullman                              5
West Ridge                                2
West Town                                22
West Town, Logan Square                  37
Woodlawn                                  2

[76 rows x 1 columns]

In [93]:
chi_num_rest[chi_num_rest['Num of Restaurants']==chi_num_rest['Num of Restaurants'].max()]

Num of Restaurants
Neighborhood                    
The Loop                      73

### One Hot Encoding for Category (Irrelevant?)

In [20]:
# one hot encoding
chi_onehot = pd.get_dummies(chi_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
chi_onehot['Neighborhood'] = chi_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [chi_onehot.columns[-1]] + list(chi_onehot.columns[:-1])
chi_onehot = chi_onehot[fixed_columns]

chi_onehot

Neighborhood  African Restaurant  American Restaurant  Arepa Restaurant  \
0      Albany Park                   0                    0                 0   
1      Albany Park                   0                    0                 0   
2      Albany Park                   0                    0                 0   
3      Albany Park                   0                    0                 0   
4      Albany Park                   0                    0                 0   
...            ...                 ...                  ...               ...   
1045  West Pullman                   0                    0                 0   
1046  West Pullman                   0                    0                 0   
1047  West Pullman                   0                    0                 0   
1048      Woodlawn                   0                    0                 0   
1049      Woodlawn                   0                    0                 0   

      Argentinian Restaurant  Asian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                          0                 0          0           0       0   
1                          0                 0          0           0       0   
2                          0                 0          0           0       0   
3                          0                 0          0           0       0   
4                          0                 0          0           0       0   
...                      ...               ...        ...         ...     ...   
1045                       0                 0          0           0       0   
1046                       0                 0          0           0       1   
1047                       0                 0          0           0       0   
1048                       0                 0          1           0       0   
1049                       0                 0          0           0       0   

      Bistro  ...  Taco Place  Tapas Restaurant  Tex-Mex Restaurant  \
0          0  ...           0                 0                   0   
1          0  ...           0                 0                   0   
2          0  ...           0                 0                   0   
3          0  ...           0                 0                   0   
4          0  ...           0                 0                   0   
...      ...  ...         ...               ...                 ...   
1045       0  ...           0                 0                   0   
1046       0  ...           0                 0                   0   
1047       0  ...           0                 0                   0   
1048       0  ...           0                 0                   0   
1049       0  ...           0                 0                   0   

      Thai Restaurant  Theme Restaurant  Turkish Restaurant  \
0                   0                 0                   0   
1                   0                 0                   0   
2                   0                 0                   0   
3                   0                 0                   0   
4                   0                 0                   0   
...               ...               ...                 ...   
1045                0                 0                   0   
1046                0                 0                   0   
1047                0                 0                   0   
1048                0                 0                   0   
1049                0                 0                   0   

      Ukrainian Restaurant  Vegetarian / Vegan Restaurant  \
0                        0                              0   
1                        0                              0   
2                        0                              0   
3                        0                              0   
4                        0                              0   
...                    ...                            ...   
1045                   

In [21]:
chi_grouped = chi_onehot.groupby('Neighborhood').mean().reset_index()
chi_grouped

Neighborhood  African Restaurant  American Restaurant  \
0               Albany Park                 0.0               0.0000   
1            Archer Heights                 0.0               0.0000   
2             Armour Square                 0.0               0.0625   
3                   Ashburn                 0.0               0.0000   
4            Auburn Gresham                 0.0               0.0000   
..                      ...                 ...                  ...   
71             West Pullman                 0.0               0.0000   
72               West Ridge                 0.0               0.0000   
73                West Town                 0.0               0.0000   
74  West Town, Logan Square                 0.0               0.0000   
75                 Woodlawn                 0.0               0.0000   

    Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  BBQ Joint  \
0                0.0                     0.0          0.000000   0.000000   
1                0.0                     0.0          0.000000   0.000000   
2                0.0                     0.0          0.125000   0.000000   
3                0.0                     0.0          0.000000   0.200000   
4                0.0                     0.0          0.000000   0.000000   
..               ...                     ...               ...        ...   
71               0.0                     0.0          0.000000   0.000000   
72               0.0                     0.0          0.500000   0.000000   
73               0.0                     0.0          0.000000   0.045455   
74               0.0                     0.0          0.027027   0.000000   
75               0.0                     0.0          0.000000   0.500000   

    Bagel Shop    Bakery  Bistro  ...  Taco Place  Tapas Restaurant  \
0          0.0  0.000000     0.0  ...    0.090909               0.0   
1          0.0  0.076923     0.0  ...    0.000000               0.0   
2          0.0  0.125000     0.0  ...    0.000000               0.0   
3          0.0  0.000000     0.0  ...    0.000000               0.0   
4          0.0  0.000000     0.0  ...    0.000000               0.0   
..         ...       ...     ...  ...         ...               ...   
71         0.0  0.200000     0.0  ...    0.000000               0.0   
72         0.0  0.000000     0.0  ...    0.000000               0.0   
73         0.0  0.045455     0.0  ...    0.090909               0.0   
74         0.0  0.054054     0.0  ...    0.000000               0.0   
75         0.0  0.000000     0.0  ...    0.000000               0.0   

    Tex-Mex Restaurant  Thai Restaurant  Theme Restaurant  Turkish Restaurant  \
0                  0.0              0.0               0.0                 0.0   
1                  0.0              0.0               0.0                 0.0   
2                  0.0              0.0               0.0                 0.0   
3                  0.0              0.0               0.0                 0.0   
4                  0.0              0.0               0.0                 0.0   
..                 ...              ...               ...                 ...   
71                 0.0              0.0               0.0                 0.0   
72                 0.0              0.0               0.0                 0.0   
73                 0.0              0.0               0.0                 0.0   
74                 0.0              0.0               0.0                 0.0   
75                 0.0              0.0               0.0                 0.0   

    Ukrainian Restaurant  Vegetarian / Vegan Restaurant  \
0               0.000000                       0.000000   
1               0.000000                       0.000000   
2               0.000000                       0.000000   
3               0.000000                       0.000000   
4               0.000000                       0.000000   
..                   ...                     

### Restaurant Depot - Competitor info

Restaurant Depot is a competitor in the market, so we want to find their locations around the Chicago area. We will using web scraping methods to extract coordinates of all their locations and find out which stores are within 50 miles of Chicago.

In [153]:
from requests import get
url = 'https://www.restaurantdepot.com/locations/find-a-warehouse'
response = get(url)

In [154]:
from bs4 import BeautifulSoup
html_soup = BeautifulSoup(response.text, 'html.parser')
type(html_soup)

bs4.BeautifulSoup

In [156]:
location_containers = html_soup.find_all('div', class_ = 'location')
print(type(location_containers))
print(len(location_containers))

<class 'bs4.element.ResultSet'>
138


In [157]:
first_location = location_containers[0]
first_location

<div class="location" data-distance="108.04" data-id="ff001773-1dff-6ddb-b37c-ff0000940c19" data-lat="33.4478213" data-lng="-86.8242086">
<div class="container">
<h3 id="ff001773-1dff-6ddb-b37c-ff0000940c19">Birmingham, AL</h3>
<div class="col-sm-6 location-info">
<div class="address">
126 Wildwood Parkway <br/>                                        Homewood (Birmingham)<span>,</span> AL 35209                                    </div>
<div class="location-directions">
<a href="https://www.google.com/maps/dir/current+location/126+Wildwood+Parkway+Homewood+(Birmingham)+AL+35209/" target="_blank">Get Directions</a>
</div>
<div class="location-contact">
<span>Phone:</span> <a href="tel:2059422211">(205) 942-2211</a><br/> </div>
<a class="flyer" href="https://www.restaurantdepot.com/docs/default-source/regional-flyers/rd---nov-2020/nov20-midstates.pdf?sfvrsn=a9ee58b1_4" target="_blank">Flyer</a>
</div>
<div class="col-sm-6">
<a class="btn btnlocation btn-makeMyStore" data-storeid="ff001773

In [172]:
RD_lat = []
RD_lng = []

for i in range(len(location_containers)):
    lat = location_containers[i]['data-lat']
    lng = location_containers[i]['data-lng']
    
    RD_lat.append(lat)
    RD_lng.append(lng)

In [177]:
competitor_locs = pd.DataFrame({'Lat': RD_lat, 'Lng':RD_lng})
competitor_locs

Lat           Lng
0    33.4478213   -86.8242086
1    33.3799525  -111.8480504
2    33.4922156  -112.1143083
3    32.2052187  -110.9780893
4    33.8564872  -117.8601145
..          ...           ...
133  36.8473168   -76.1565419
134  47.2456363  -122.3475309
135  47.5688502  -122.3377981
136  47.7825523  -122.1497494
137  43.0064967   -87.9114213

[138 rows x 2 columns]

In [181]:
for i, row in competitor_locs.iterrows():
    coords_1 = (latitude, longitude)
    coords_2 = (row['Lat'], row['Lng'])
    
    competitor_locs.loc[i,'Dist'] = geopy.distance.distance(coords_1, coords_2).miles

In [184]:
# We only want stores that within 50 miles the center of our neighborhoods
competitor_locs = competitor_locs[competitor_locs.Dist < 50].reset_index(drop=True)
competitor_locs

Lat          Lng       Dist
0  41.6629194  -87.7182809  12.782809
1  41.9047161  -87.6542859   4.252172
2  41.8781136  -87.6297982   3.332029
3  42.0137498  -87.8882926  15.894239
4  41.9063008  -88.0347802  18.896216

In [185]:
competitor_dist = pd.DataFrame()

for lat, lng, neighborhood in zip(neighborhood_loc_data['Latitude'], neighborhood_loc_data['Longitude'], neighborhood_loc_data['Neighborhood']):
    coords_1 = (lat, lng)
    for i, row in competitor_locs.iterrows():
        coords_2 = (row['Lat'], row['Lng'])

        competitor_dist.loc[i,neighborhood] = geopy.distance.distance(coords_1, coords_2).miles

In [186]:
competitor_dist

Albany Park  Riverdale  Edgewater  Archer Heights  Armour Square  \
0    21.327272   5.873921  22.293143       10.256909      12.991904   
1     5.629767  16.545715   5.451184        7.430502       4.595896   
2     7.858125  14.569001   7.474596        6.776261       2.633690   
3     9.319893  27.995713  11.738368       16.274167      17.796802   
4    17.031302  27.635832  19.833653       17.216766      21.218324   

     Ashburn  Auburn Gresham  Avalon Park   Avondale  Irving Park  ...  \
0   5.851145        6.418910     8.778325  19.051871    20.067162  ...   
1  11.238378       11.134579    11.529490   3.764191     5.404068  ...   
2   9.943122        9.396417     9.426943   5.933833     7.562905  ...   
3  20.519280       22.173744    24.140969  10.482457     8.860505  ...   
4  19.978236       22.553669    25.577838  16.831311    15.714728  ...   

    Lakeview  South Chicago  South Deering  Washington Park  West Elsdon  \
0  19.674624       9.951786       7.849194        10.336374     9.046765   
1   2.705647      12.888726      15.271932         7.964295     8.461500   
2   4.710934      10.702338      13.174646         5.937108     7.592933   
3  12.988971      25.948589      27.554177        20.667841    17.363784   
4  19.793028      27.629359      28.109807        22.890118    17.790717   

   West Englewood  West Garfield Park  Austin, Humboldt Park  West Pullman  \
0        8.383594           15.033014              16.068639      4.180790   
1        8.762786            4.207838               4.520038     16.097485   
2        7.161487            5.130980               5.854070     14.247304   
3       19.876470           12.314076              11.162741     26.896251   
4       20.954886           15.856256              15.167040     26.100278   

    Woodlawn  
0  10.120950  
1   9.094178  
2   6.984787  
3  21.981492  
4  24.109005  

[5 rows x 80 columns]

52e816a6bcbc57f1066b7a54We'll use the Foursquare category ID for any food related venue (4d4b7105d754a06374d81259). Also, we will use Warehouse Store category (52e816a6bcbc57f1066b7a54) to find competitors. (https://developer.foursquare.com/docs/build-with-foursquare/categories/)